# Início

In [2]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import copy
from tqdm import tqdm
import time
import os
from scipy import signal
from scipy.signal import find_peaks
from scipy.spatial import distance
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA

In [8]:
files = ['acc_climbingup_forearm.csv',
         'acc_climbingup_thigh.csv',
         'acc_walking_forearm.csv',
         'acc_walking_thigh.csv']
data = pd.read_csv(files[2])

In [9]:
px.line(data.iloc[:,2:])

In [10]:
def picotar(x, J, passo):
    N = x.shape[0]
    Nj = (N-J)//passo + 1
    X = np.zeros((Nj, J))
    for i in range(Nj):
        X[i,:] = x[(i*passo):(i*passo+J)]
    return X

In [11]:
def pcabase(X):
    M = np.ones((X.shape[0],1)).dot(X.mean(axis=0).reshape(1,X.shape[1]))
    R = (X-M).transpose().dot(X-M)
    l, vet = np.linalg.eig(R)
    inds = np.argsort(l)
    vet = vet[:,inds][:,::-1]
    return l, vet

In [23]:
def predlin3d(Xtr):
    X = Xtr[:,:-3]
    y1 = Xtr[:,-1]
    y2 = Xtr[:,-2]
    y3 = Xtr[:,-3]
    pX = np.linalg.inv(X.transpose().dot(X)).dot(X.transpose())
    w1 = pX.dot(y1)
    w2 = pX.dot(y2)
    w3 = pX.dot(y3)
    return w1, w2, w3

In [43]:
s = data.iloc[:,2:].values.reshape(-1)
passo = 3
J = 1*passo
X = picotar(s, J, passo)
w1, w2, w3 = predlin3d(X)
y1h = X[:,:-3].dot(w1)
y2h = X[:,:-3].dot(w2)
y3h = X[:,:-3].dot(w3)

In [44]:
w1

array([], dtype=float64)

In [36]:
erro = X[:,-3:] - np.vstack((y3h, y2h, y1h)).transpose()
np.sqrt(np.sum(erro**2, axis=1)).mean()

0.6847244418279295

In [40]:
Em = []
Em.append(np.sqrt(np.sum(data.iloc[:,2:].values**2, axis=1)).mean())
passo = 3
for i in np.arange(1,150):
    J = i*passo
    X = picotar(s, J, passo)
    w1, w2, w3 = predlin3d(X)
    y1h = X[:,:-3].dot(w1)
    y2h = X[:,:-3].dot(w2)
    y3h = X[:,:-3].dot(w3)
    erro = X[:,-3:] - np.vstack((y3h, y2h, y1h)).transpose()
    Em.append(np.sqrt(np.sum(erro**2, axis=1)).mean())

In [42]:
px.scatter(Em)

In [29]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=X[:,-1], mode='lines', showlegend=True, name='1original'))
fig.add_trace(go.Scatter(y=y1h, mode='lines', showlegend=True, name='1predição'))
fig.add_trace(go.Scatter(y=X[:,-2], mode='lines', showlegend=True, name='2original'))
fig.add_trace(go.Scatter(y=y2h, mode='lines', showlegend=True, name='2predição'))
fig.add_trace(go.Scatter(y=X[:,-3], mode='lines', showlegend=True, name='3original'))
fig.add_trace(go.Scatter(y=y3h, mode='lines', showlegend=True, name='3predição'))

In [ ]:
J = 150
passo = 150
X = picotar(s[0], J, passo)
l, vet = pcabase(X)
fig = px.line(vet[:,:5], range_y=[-1/5,1/5])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [ ]:
d = 30
W = vet[:,:d]
i = 100
X = picotar(s[1], J, passo)
x = X[i,:]
S = x.dot(W)
xh = S.dot(W.transpose())
fig = go.Figure()
fig.add_trace(go.Scatter(y=x, mode='lines', showlegend=True, name='original'))
fig.add_trace(go.Scatter(y=xh, mode='lines', showlegend=True, name='reconstrução'))

In [ ]:
def predlin(Xtr):
    X = Xtr[:,:-1]
    y = Xtr[:,-1]
    w = np.linalg.inv(X.transpose().dot(X)).dot(X.transpose()).dot(y)
    return w

# Pegando os dados

In [59]:
pasta = 'C:\\Meu Drive\\Doutorado Unicamp\\Projeto\\Dataset\\realworldcsvs\\proband1\\acc\\'
vals = []
for file in os.listdir(pasta):
    data = pd.read_csv(pasta+file)
    vals.append(len(data))

In [61]:
fig = px.scatter(np.array(vals))
fig.update_layout(
    xaxis = dict(
        tickvals = np.arange(56),
        ticktext = os.listdir(pasta)
    )
)

In [62]:
tarefas = ['climbingdown', 'climbingup', 'lying', 'running', 'sitting', 'standing', 'walking']
posicao = ['chest', 'forearm', 'head', 'shin', 'thigh', 'upperarm', 'waist']

In [ ]:
for dom in posicao:
    